In [1]:
import pandas as pd

df = pd.read_csv('raw/bq-results-20211206-133858-irtkgx60el7i.csv').drop(['ParentUrl', 'ParentAuthor', 'ParentTime', 'ParentScore'], axis=1)

# There's a mix of HTML, sanitized links and raw Unicode that we'd like to clean up
df.text = df.text.str.replace('<p>', '\n')
strings_to_remove = ['rel="nofollow"', '<pre>', '</pre>', '<i>', '</i>', '<code>', '</code>', '&gt;']
email_regex = '[a-zA-Z0-9._-]{0,30}@[a-zA-Z0-9._-]{0,20}\.[a-zA-Z0-9_-]{2,3}' # for redacting emails
munged_url_regex = 'http(s)?:\&\#.*?\<\/a>'

for string in strings_to_remove:
    df.text = df.text.str.replace(string, '')


df.text = df.text.replace(email_regex, 'REDACTED_EMAIL', regex=True)
df.text = df.text.replace(munged_url_regex, '', regex=True)

    # fix some unicode issues
df.text = df.text.str.replace('&#x27;', "'")
df.text = df.text.str.replace('&#x2F;', "/")
df.text = df.text.str.replace("&quot;", '"')

hiring_df = df[df.ParentTitle.str.lower().str.contains('who is hiring')]
wants_to_be_hired_df = df[df.ParentTitle.str.lower().str.contains('wants to be hired')]
freelancer_df = df[df.ParentTitle.str.lower().str.contains('freelancer')]


/usr/local/anaconda3/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3165: DtypeWarning: Columns (4) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


In [2]:
import datasets
from huggingface_hub import create_repo
from huggingface_hub import Repository

all_datasets = datasets.dataset_dict.DatasetDict({'hiring': datasets.Dataset.from_pandas(hiring_df).remove_columns('__index_level_0__'),
                                                  'wants_to_be_hired': datasets.Dataset.from_pandas(wants_to_be_hired_df).remove_columns('__index_level_0__'),
                                                  'freelancer': datasets.Dataset.from_pandas(freelancer_df).remove_columns('__index_level_0__')})
data_path = './data'
all_datasets.save_to_disk(data_path)

repo_url = 'https://huggingface.co/datasets/dansbecker/hackernews_hiring_posts'
repo = Repository(local_dir=".", clone_from=repo_url)
repo.git_add(data_path)
repo.git_add('*.ipynb') # This file
repo.git_add('README.md')
repo.push_to_hub(commit_message='Regular update', blocking=True, clean_ok=False)

/Users/dan.becker/Desktop/hackernews_hiring_dataset/. is already a clone of https://huggingface.co/datasets/dansbecker/hackernews_hiring_posts. Make sure you pull the latest changes with `repo.git_pull()`.
Several commits (5) will be pushed upstream.
The progress bars may be unreliable.


Upload file data/hiring/dataset.arrow:   0%|          | 32.0k/78.2M [00:00<?, ?B/s]

Upload file data/wants_to_be_hired/dataset.arrow:   0%|          | 32.0k/10.8M [00:00<?, ?B/s]

Upload file data/freelancer/dataset.arrow:   0%|          | 32.0k/10.6M [00:00<?, ?B/s]

remote: ----------------------------------------------------------        
remote: Your push was accepted, but with warnings:        
remote: - warning : empty or missing yaml metadata in card (dansbecker/hackernews_hiring_posts)        
remote: help: please find help at https://huggingface.co/docs/hub/model-repos        
remote: ----------------------------------------------------------        
remote: Please find the documentation at:        
remote: https://huggingface.co/docs/hub/model-repos(B        
remote: ----------------------------------------------------------        
remote: -------------------------------------------------------------------------        
remote: Your push was rejected because it contains files larger than 10M.        
remote: Please use https://git-lfs.github.com/ to store larger files.(B        
remote: -------------------------------------------------------------------------        
remote: Offending files:        
remote:  - raw/bq-results-2021120

OSError: remote: ----------------------------------------------------------[33m        
remote: Your push was accepted, but with warnings:        
remote: - warning : empty or missing yaml metadata in card (dansbecker/hackernews_hiring_posts)        
remote: help: please find help at https://huggingface.co/docs/hub/model-repos[32m        
remote: ----------------------------------------------------------        
remote: Please find the documentation at:        
remote: https://huggingface.co/docs/hub/model-repos(B[m        
remote: ----------------------------------------------------------        
remote: -------------------------------------------------------------------------[31m        
remote: Your push was rejected because it contains files larger than 10M.        
remote: Please use https://git-lfs.github.com/ to store larger files.(B[m        
remote: -------------------------------------------------------------------------        
remote: Offending files:        
rem